In [19]:
import numpy as np
import pandas as pd
import datetime as dt
from scipy import stats
import plotly.express as px
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
import seaborn as sns
import json
import ast
from sklearn.model_selection import StratifiedShuffleSplit
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score, accuracy_score
from sklearn.model_selection import train_test_split
import statsmodels.api as sm
import ast
from collections import Counter
from scipy.sparse import csr_matrix
from sklearn.neighbors import NearestNeighbors, NearestCentroid, KNeighborsClassifier
from sklearn.model_selection import train_test_split
import random
# from skmultilearn.model_selection import iterative_train_test_split

# Collaborative Filtering

In [20]:
df = pd.read_csv('lastfm_user_clean.csv')
df.head()

Username                                             Top_50  \
0          emosoup  [('Higher', 'Sleep Token', '1', '1321'), ('The...   
1        gibelotte  [('DAYWALKER! (feat. Corpse)', 'Machine Gun Ke...   
2         riddy_pr  [('Will We Talk?', 'Sam Fender', '1', '291'), ...   
3  TheGirlNamedSig  [('Be Quiet and Drive (Far Away)', 'Deftones',...   
4      eventually_  [('Light', 'Tag Shai', '1', '6142'), ('Old You...   

                                               Loved  playcount  artist_count  \
0  [('Obsidian', 'Viscera'), ('yes, and?', 'Arian...     187276          3386   
1  [('Fragile', 'Young Cub'), ("Sarabeth's Song",...      96134          4453   
2                                                 []      46389          2495   
3  [("Beaver O'Lindy", 'Sparks'), ('Age of Consen...      34006          2380   
4  [('Clock Hands', 'Harlow Road'), ('Waterslides...     459131         12363   

   track_count  album_count         country        type  registered_year  \
0        13520         6171   United States  subscriber             2015   
1        13123         6514   United States        user             2013   
2        11923         5189  United Kingdom        user             2018   
3         6994         3987             NaN        user             2017   
4        57910        15197   United States  subscriber             2013   

   registered_month  registered_day  
0                 8              31  
1                11               7  
2                12              31  
3                 1              10  
4                12               1

In [21]:
# Create lists to store the new data
user_ids = []
track_artists = []
rankings = []
total_rating_counts = []
playcount_proportions = []

# Iterate through each row (user) in the DataFrame
for index, row in df.iterrows():
    username = row['Username']
    top_50 = ast.literal_eval(row['Top_50'])
    total_playcount = sum(int(song[3]) for song in top_50)
    
    # Iterate through each song in the 'Top_50' list
    for song in top_50:
        trackname = song[0]
        artistname = song[1]
        rank = int(song[2])
        playcount = int(song[3])
        
        # Calculate playcount proportion
        playcount_proportion = playcount / total_playcount
        
        # Append data to the lists
        user_ids.append(username)
        track_artists.append(f"{trackname} - {artistname}")
        rankings.append(rank)
        playcount_proportions.append(playcount_proportion)

# Create a new DataFrame with the collected data
knn_df = pd.DataFrame({
    'Username': user_ids,
    'Track_Artist': track_artists,
    'Ranking': rankings,
    'PlaycountProportion': playcount_proportions
})

# Display the new DataFrame
print(knn_df)

         Username                                      Track_Artist  Ranking  \
0         emosoup                              Higher - Sleep Token        1   
1         emosoup                   The Love You Want - Sleep Token        2   
2         emosoup                          Dark Signs - Sleep Token        3   
3         emosoup                            Alkaline - Sleep Token        4   
4         emosoup    The Night Does Not Belong to God - Sleep Token        5   
...           ...                                               ...      ...   
498250  cow_puppy    Solar Mirror Anthology Vol. 6 - Sound of Ceres       46   
498251  cow_puppy       Out By 16, Dead on the Scene - Machine Girl       47   
498252  cow_puppy  Outlook Remains Untouched - ||||||||||||||||||||       48   
498253  cow_puppy                             Flood, Part 1 - Boris       49   
498254  cow_puppy                             Flood, Part 2 - Boris       50   

        PlaycountProportion  
0        

In [22]:
# Group by Track_Artist and count occurrences
song_counts = knn_df.groupby('Track_Artist').size().reset_index(name='TotalSongCount')

# Merge counts back to the original DataFrame
knn_df = pd.merge(knn_df, song_counts, on='Track_Artist', how='left')

# Sort the DataFrame by Username and reset index
knn_df = knn_df.sort_values(by='Username').reset_index(drop=True)

print(knn_df)
knn_df.head()

           Username                       Track_Artist  Ranking  \
0        -Dolorosa-         Feral Love - Chelsea Wolfe       37   
1        -Dolorosa-      Such Small Hands - La Dispute       27   
2        -Dolorosa-                 Shadows - Warpaint       28   
3        -Dolorosa-                     Intro - Bonobo       29   
4        -Dolorosa-      Quiet - This Will Destroy You       31   
...             ...                                ...      ...   
498250  zzakkkkkkkk                 Secrets - The Cure       30   
498251  zzakkkkkkkk               Less Sex - Daughters       29   
498252  zzakkkkkkkk          Flatlands - Chelsea Wolfe       28   
498253  zzakkkkkkkk         The Real - John Frusciante       26   
498254  zzakkkkkkkk  Could Never Be Heaven - Brand New       35   

        PlaycountProportion  TotalSongCount  
0                  0.016668              10  
1                  0.017497              37  
2                  0.017497               8  
3          

Username                   Track_Artist  Ranking  PlaycountProportion  \
0  -Dolorosa-     Feral Love - Chelsea Wolfe       37             0.016668   
1  -Dolorosa-  Such Small Hands - La Dispute       27             0.017497   
2  -Dolorosa-             Shadows - Warpaint       28             0.017497   
3  -Dolorosa-                 Intro - Bonobo       29             0.017405   
4  -Dolorosa-  Quiet - This Will Destroy You       31             0.017405   

   TotalSongCount  
0              10  
1              37  
2               8  
3               7  
4              10

In [23]:
bottom_5_percent_threshold = knn_df['TotalSongCount'].quantile(0.05)
# Filter the DataFrame for values below the threshold
popular_song_df = knn_df[knn_df['TotalSongCount'] > bottom_5_percent_threshold]

print(popular_song_df)

print(f"Number of rows removed: {498255-346103}")
popular_song_df.head()

           Username                       Track_Artist  Ranking  \
0        -Dolorosa-         Feral Love - Chelsea Wolfe       37   
1        -Dolorosa-      Such Small Hands - La Dispute       27   
2        -Dolorosa-                 Shadows - Warpaint       28   
3        -Dolorosa-                     Intro - Bonobo       29   
4        -Dolorosa-      Quiet - This Will Destroy You       31   
...             ...                                ...      ...   
498249  zzakkkkkkkk                Screen Shot - Swans       31   
498250  zzakkkkkkkk                 Secrets - The Cure       30   
498251  zzakkkkkkkk               Less Sex - Daughters       29   
498252  zzakkkkkkkk          Flatlands - Chelsea Wolfe       28   
498254  zzakkkkkkkk  Could Never Be Heaven - Brand New       35   

        PlaycountProportion  TotalSongCount  
0                  0.016668              10  
1                  0.017497              37  
2                  0.017497               8  
3          

Username                   Track_Artist  Ranking  PlaycountProportion  \
0  -Dolorosa-     Feral Love - Chelsea Wolfe       37             0.016668   
1  -Dolorosa-  Such Small Hands - La Dispute       27             0.017497   
2  -Dolorosa-             Shadows - Warpaint       28             0.017497   
3  -Dolorosa-                 Intro - Bonobo       29             0.017405   
4  -Dolorosa-  Quiet - This Will Destroy You       31             0.017405   

   TotalSongCount  
0              10  
1              37  
2               8  
3               7  
4              10

In [24]:
# Create a mapping dictionary for unique Track_Artists
unique_track_artists = popular_song_df['Track_Artist'].unique()
unique_username = popular_song_df['Username'].unique()
track_artist_to_songid = {artist: i for i, artist in enumerate(unique_track_artists)}
username_to_userid = {username: i for i, username in enumerate(unique_username)}
print(track_artist_to_songid)
print(username_to_userid)

# Add a new column 'UserID' by mapping Track_Artist to UserID
popular_song_df['SongID'] = popular_song_df['Track_Artist'].map(track_artist_to_songid)
popular_song_df['UserID'] = popular_song_df['Username'].map(username_to_userid)
popular_song_df.head()

{'Feral Love - Chelsea Wolfe': 0, 'Such Small Hands - La Dispute': 1, 'Shadows - Warpaint': 2, 'Intro - Bonobo': 3, 'Quiet - This Will Destroy You': 4, 'Bloodhail - Have a Nice Life': 5, 'Cover the Roots / Lower the Stems - Moving Mountains': 6, 'No Waves - FIDLAR': 7, 'Mer - Chelsea Wolfe': 8, 'Wet Hair - Japandroids': 9, 'Rock & Roll Queen - The Subways': 10, 'Feels Like We Only Go Backwards - Tame Impala': 11, 'Dog - Wavves': 12, 'Royals - Lorde': 13, 'VCR - The xx': 14, 'Young Hearts Spark Fire - Japandroids': 15, 'Lobby - The Kilimanjaro Darkjazz Ensemble': 16, 'Memorial (feat. Chelsea Wolfe) - Russian Circles': 17, 'Flatlands - Chelsea Wolfe': 18, 'Crystalised - The xx': 19, 'Moses - Chelsea Wolfe': 20, 'I Will Follow You Into The Dark - Death Cab for Cutie': 21, 'We Hit a Wall - Chelsea Wolfe': 22, 'Teardrop - Massive Attack': 23, 'everything is fine - Teen Suicide': 24, 'Brighter Than Anything - Yonderboi': 25, 'Wretched World - Converge': 26, 'King of the Beach - Wavves': 27, 

/var/folders/w3/p_0x2kls1sb4qpyv2ch25z6c0000gn/T/ipykernel_18522/630299520.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  popular_song_df['SongID'] = popular_song_df['Track_Artist'].map(track_artist_to_songid)
/var/folders/w3/p_0x2kls1sb4qpyv2ch25z6c0000gn/T/ipykernel_18522/630299520.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  popular_song_df['UserID'] = popular_song_df['Username'].map(username_to_userid)


Username                   Track_Artist  Ranking  PlaycountProportion  \
0  -Dolorosa-     Feral Love - Chelsea Wolfe       37             0.016668   
1  -Dolorosa-  Such Small Hands - La Dispute       27             0.017497   
2  -Dolorosa-             Shadows - Warpaint       28             0.017497   
3  -Dolorosa-                 Intro - Bonobo       29             0.017405   
4  -Dolorosa-  Quiet - This Will Destroy You       31             0.017405   

   TotalSongCount  SongID  UserID  
0              10       0       0  
1              37       1       0  
2               8       2       0  
3               7       3       0  
4              10       4       0

In [25]:
unique_song_lst = popular_song_df['Track_Artist'].unique().tolist()

# Set a seed for reproducibility
random.seed(42)

# Calculate the number of elements to take (20% of the list)
num_to_take = int(len(unique_song_lst) * 0.2)

# Shuffle the list in-place
random.shuffle(unique_song_lst)

# Take the first 20% of the shuffled list
taken_items = unique_song_lst[:num_to_take]

# The remaining 80%
remaining_items = unique_song_lst[num_to_take:]

print("Original List:", unique_song_lst)
print("Randomly Taken 20%:", taken_items)
print("Remaining 80%:", remaining_items)

Original List: ["Bird's Nest - Jordaan Mason & the Horse Museum", 'The Dress - Dijon', 'Fulenn - Alvan', 'March to the Sea - twenty one pilots', 'Rafting Starlit Everglades - Baths', 'My Mom - Kimya Dawson', 'Dope - BTS', 'Prelude To Repulsion - Suffocation', 'Out For Blood - Code Orange', "Let's Build a Car - Swell Maps", 'They Declare It - Discharge', 'Let It Bleed - The Used', 'Love Struck - V Factory', 'Defleshed - The Partisan Turbine', 'Mad Stalkers - 21 Savage', 'Oversleepers International - Emperor X', 'goodnight n go - Ariana Grande', 'Use My Voice - Evanescence', 'Doncamatic (feat. Daley) - Gorillaz', 'Debris Slide - Pavement', 'Embrasa - BRAZA', 'Tweaks ~ Heavy cloud but no rain - GWSN', 'Untenkutoja - Moonlight Sorcery', 'Deeper - Freddie Gibbs', 'Fighting - Alex G', 'Accidental Babies - Damien Rice', 'Humans Being - Van Halen', 'Wreck Lanes - The Casper Fight Scene', 'Wolf Moon (Including Zoanthropic Paranoia) - Type O Negative', 'Hejira - Joni Mitchell', 'Running Free - I

In [26]:
train = popular_song_df[popular_song_df['Track_Artist'].isin(taken_items)]
test = popular_song_df[popular_song_df['Track_Artist'].isin(remaining_items)]
print(len(train))
print(len(test))

67715
278388


In [27]:
# create a pivot matrix
popular_song_pivot = popular_song_df.pivot_table(index='Track_Artist',columns='UserID',values='PlaycountProportion').fillna(0)
print(popular_song_pivot.shape)

(60343, 9964)


In [28]:
popular_song_pivot

UserID                                              0     1     2     3     \
Track_Artist                                                                 
! - Trippie Redd                                     0.0   0.0   0.0   0.0   
!? - lungskull                                       0.0   0.0   0.0   0.0   
!Ed Buys Houses! - Sidney Gish                       0.0   0.0   0.0   0.0   
"...inside the house was getting darker" - bedbug    0.0   0.0   0.0   0.0   
"45" - The Gaslight Anthem                           0.0   0.0   0.0   0.0   
...                                                  ...   ...   ...   ...   
항상 (HANGSANG) - j-hope                               0.0   0.0   0.0   0.0   
혼자 남은 지금 꼴이 - death's dynamic shroud                 0.0   0.0   0.0   0.0   
화성인 바이러스 (Boys & Girls) (feat. Key of SHINee) -...   0.0   0.0   0.0   0.0   
휘파람 - BLACKPINK                                      0.0   0.0   0.0   0.0   
흥탄소년단 (demo ver.) - BTS                              0.0   0.0   0.0   0.0   

UserID                                              4     5     6     7     \
Track_Artist                                                                 
! - Trippie Redd                                     0.0   0.0   0.0   0.0   
!? - lungskull                                       0.0   0.0   0.0   0.0   
!Ed Buys Houses! - Sidney Gish                       0.0   0.0   0.0   0.0   
"...inside the house was getting darker" - bedbug    0.0   0.0   0.0   0.0   
"45" - The Gaslight Anthem                           0.0   0.0   0.0   0.0   
...                                                  ...   ...   ...   ...   
항상 (HANGSANG) - j-hope                               0.0   0.0   0.0   0.0   
혼자 남은 지금 꼴이 - death's dynamic shroud                 0.0   0.0   0.0   0.0   
화성인 바이러스 (Boys & Girls) (feat. Key of SHINee) -...   0.0   0.0   0.0   0.0   
휘파람 - BLACKPINK                                      0.0   0.0   0.0   0.0   
흥탄소년단 (demo ver.) - BTS                              0.0   0.0   0.0   0.0   

UserID                                              8     9     ...  9954  \
Track_Artist                                                    ...         
! - Trippie Redd                                     0.0   0.0  ...   0.0   
!? - lungskull                                       0.0   0.0  ...   0.0   
!Ed Buys Houses! - Sidney Gish                       0.0   0.0  ...   0.0   
"...inside the house was getting darker" - bedbug    0.0   0.0  ...   0.0   
"45" - The Gaslight Anthem                           0.0   0.0  ...   0.0   
...                                                  ...   ...  ...   ...   
항상 (HANGSANG) - j-hope                               0.0   0.0  ...   0.0   
혼자 남은 지금 꼴이 - death's dynamic shroud                 0.0   0.0  ...   0.0   
화성인 바이러스 (Boys & Girls) (feat. Key of SHINee) -...   0.0   0.0  ...   0.0   
휘파람 - BLACKPINK                                      0.0   0.0  ...   0.0   
흥탄소년단 (demo ver.) - BTS                              0.0   0.0  ...   0.0   

UserID                                              9955  9956  9957  9958  \
Track_Artist                                                                 
! - Trippie Redd                                     0.0   0.0   0.0   0.0   
!? - lungskull                                       0.0   0.0   0.0   0.0   
!Ed Buys Houses! - Sidney Gish                       0.0   0.0   0.0   0.0   
"...inside the house was getting darker" - bedbug    0.0   0.0   0.0   0.0   
"45" - The Gaslight Anthem                           0.0   0.0   0.0   0.0   
...                                                  ...   ...   ...   ...   
항상 (HANGSANG) - j-hope                               0.0   0.0   0.0   0.0   
혼자 남은 지금 꼴이 - death's dynamic shroud                 0.0   0.0   0.0   0.0   
화성인 바이러스 (Boys & Girls) (feat. Key of SHINee) -...   0.0   0.0   0.0   0.0   
휘파람 - BLACKPINK                                      0.0   0.0   0.0   0.0   
흥탄소년단 (demo ver.) - BTS         

In [29]:
popular_song_matrix = csr_matrix(popular_song_pivot.values)
model_knn = NearestNeighbors(metric = 'cosine', algorithm = 'brute')
model_knn.fit(popular_song_matrix)

NearestNeighbors(algorithm='brute', metric='cosine')

In [30]:
query_index = np.random.choice(popular_song_pivot.shape[0])
distances, indices = model_knn.kneighbors(popular_song_pivot.iloc[query_index,:].values.reshape(1, -1), n_neighbors = 6)

In [31]:
for i in range(0, len(distances.flatten())):
    if i == 0:
        print('Recommendations for {0}:\n'.format(popular_song_pivot.index[query_index]))
    else:
        print('{0}: {1}, with distance of {2}:'.format(i, popular_song_pivot.index[indices.flatten()[i]], distances.flatten()[i]))

Recommendations for Snowflake - Kate Bush:

1: Those Were the Days - Angel Olsen, with distance of 0.3672836013077162:
2: And I Remember Every Kiss - Jens Lekman, with distance of 0.399552868252657:
3: Sex Yeah - Marina & the Diamonds, with distance of 0.5170644928197694:
4: Goodbye England (Covered in Snow) - Laura Marling, with distance of 0.5243491986869531:
5: Saved These Words - Laura Marling, with distance of 0.5296686305161546:
